### Topic modeling/ comparing with tf-idf

In [2]:
import pandas as pd
import nltk
import re
import requests
import json
import io
import matplotlib.pyplot as plt
import numpy as np
import os.path
from sklearn.feature_extraction.text import TfidfVectorizer
import matplotlib.pyplot as plt
from sklearn.metrics import ConfusionMatrixDisplay

In [3]:
noscemus_metadata = pd.read_csv('res_df.csv')
noscemus_metadata.head(5)

Unnamed: 0             Author  \
0           0  Achrelius, Daniel   
1           1  Acidalius, Valens   
2           3  Acidalius, Valens   
3           5    Acosta, José de   
4           6     Adam, Melchior   

                                          Full title  \
0  Scientiarum magnes recitatus publice anno 1690...   
1                 Ad Iordanum Brunum Nolanum, Italum   
2                 Ad Iordanum Brunum Nolanum, Italum   
3  De natura novi orbis libri duo et De promulgat...   
4  Vitae Germanorum medicorum, qui saeculo superi...   

                                                  In  Year       Place  \
0                                                NaN  1690     [Turku]   
1  Poematum Iani Lernutii, Iani Gulielmi, Valenti...  1603    Liegnitz   
2  Poematum Iani Lernutii, Iani Gulielmi, Valenti...  1603     Wrocław   
3                                                NaN  1589   Salamanca   
4                                                NaN  1620  Heidelberg   

  Publisher/Printer           Era      Form/Genre  \
0              Wall  17th century         Oration   
1     Albert, David  17th century  Panegyric poem   
2     Albert, David  17th century  Panegyric poem   
3  Guillelum Foquel  16th century       Monograph   
4      Rosa, Geyder  17th century       Biography   

                                            Original  ... Chemistry  \
0                   Scientiarum magnes(Google Books)  ...         0   
1  Ad Iordanum Brunum (1603)(CAMENA)Ad Iordanum B...  ...         1   
2  Ad Iordanum Brunum (1603)(CAMENA)Ad Iordanum B...  ...         1   
3  De natura novi orbis(Biodiversity Heritage Lib...  ...         1   
4  Vitae Germanorum medicorum(MDZ)Alternative lin...  ...         1   

  Mathematics Meteorology Earth-sciences Cosmography Astronomy Biology Other  \
0           0           0              1           0         0       0     0   
1           1           1              1           0         0       1     1   
2           1           1              1           0         0       1     1   
3           1           0              1           0         0       1     1   
4           1           1              1           1         1       1     1   

  NaN Geography  
0   1         1  
1   1         1  
2   1         1  
3   1         0  
4   1         1  

[5 rows x 42 columns]

In [4]:
'''os.mkdir('texts')
for index, row in noscemus_metadata.iterrows():
    id = row['id']
    base_url = "https://ccs-lab.zcu.cz/noscemus_sents_data/{}.json"
    try:
        res = requests.get(base_url.format(str(id))).json()      
        #res = json.load(io.BytesIO(requests.get(base_url.format(str(id))).content))
        print(id)
        #Load json string to json object
        json_object = json.dumps(res)

        # Writing to sample.json
        with open(f"{id}.json", "w") as outfile:
            outfile.write(json_object)        
        #load json from file
        #j_obj_loaded = json.load(open("example.json", "r"))
    except:
        print('No file')
    '''
    

'os.mkdir(\'texts\')\nfor index, row in noscemus_metadata.iterrows():\n    id = row[\'id\']\n    base_url = "https://ccs-lab.zcu.cz/noscemus_sents_data/{}.json"\n    try:\n        res = requests.get(base_url.format(str(id))).json()      \n        #res = json.load(io.BytesIO(requests.get(base_url.format(str(id))).content))\n        print(id)\n        #Load json string to json object\n        json_object = json.dumps(res)\n\n        # Writing to sample.json\n        with open(f"{id}.json", "w") as outfile:\n            outfile.write(json_object)        \n        #load json from file\n        #j_obj_loaded = json.load(open("example.json", "r"))\n    except:\n        print(\'No file\')\n    '

In [ ]:
def get_disc_ids(disc_name):
    disc_ids = []
    for index, row in noscemus_metadata.iterrows():
        if row[disc_name] == True:
            disc_ids.append(row['id'])
    return disc_ids

def flatten(xss):
    return [x for xs in xss for x in xs]

def get_json_content(disc_ids):
    res =[]
    for i in disc_ids:
        try:
            with open(f'texts/{i}.json') as f:
                f_sents_data = json.load(f)
            subset_lemmatized_sentences = []
            for sent_data in f_sents_data:
                sent_lemmata = [t[1] for t in sent_data[3]] 
                sent_lemmata = [re.sub(r"\W*|\d*", "", t) for t in sent_lemmata] # remove all non-alphanumeric characters
                #sent_lemmata = [l for l in sent_lemmata if len(l) > 1] # remove all one-letter words
                sent_lemmata = [l.lower() for l in sent_lemmata] # lowercase all words
                subset_lemmatized_sentences.append(sent_lemmata) 
            res.append(subset_lemmatized_sentences)
            print(res)
        except:
            print('no file')
    return flatten(res)

In [6]:
# from: https://www.perseus.tufts.edu/hopper/stopwords 
latin_stopwords = {
    'ab', 'ac', 'ad', 'adhic', 'aliqui', 'aliquis', 'an', 'ante', 'apud', 'at', 'atque', 'aut', 'autem', 'cum', 'cur',
    'de', 'deinde', 'dum', 'ego', 'enim', 'ergo', 'es', 'est', 'et', 'etiam', 'etsi', 'ex', 'fio', 'haud', 'hic', 'iam', 
    'idem', 'igitur', 'ille', 'in', 'infra', 'inter', 'interim', 'ipse', 'is', 'ita', 'magis', 'modo', 'mox', 'nam', 'ne',
    'nec', 'necque', 'neque', 'nisi', 'non', 'nos', 'o', 'ob', 'per', 'possum', 'post', 'pro', 'quae', 'quam', 'quare', 'qui',
    'quia', 'quicumque', 'quidem', 'quilibet', 'quis', 'quisnam', 'quisquam', 'quisque', 'quisquis', 'quo', 'quoniam', 'sed',
    'si', 'sic', 'sive', 'sub', 'sui', 'sum', 'super', 'suus', 'tam', 'tamen', 'trans', 'tu', 'tum', 'ubi', 'uel', 'uero', 'unus', 'ut'
}

def get_top_words(texts, n=10):
    # Vectorize with TF-IDF
    vectorizer = TfidfVectorizer(stop_words=list(latin_stopwords), encoding='utf-8')
    tfidf_matrix = vectorizer.fit_transform(texts)
    
    # Sum scores and extract keywords
    scores = np.asarray(tfidf_matrix.sum(axis=0)).flatten()
    features = vectorizer.get_feature_names_out()
    word_scores = sorted(zip(features, scores), key=lambda x: x[1], reverse=True)
    
    return word_scores[:n]

In [7]:
# det tf_idf for each discipline
# separate disciplines
all_disc = ['Earth', 'Mathematics', 'Other', 'Physics', 'Meteorology', 'Geography', 'Chemistry', 'NaN', 'Biology', 'Astronomy', 'Cartography', 'Cosmography', 'Medicine', 'Alchemy', 'Astrology', 'Earth-sciences', 'ids']

#for index, row in  noscemus_metadata.iterrows():
keyword_dict={}
for d in all_disc:
    # Get top keywords
    text = get_json_content(get_disc_ids(d))
    keyword_dict[d] = get_top_words(text, n=20)

print(keyword_dict)
'''
# Print results
print("Top Biology Keywords:")
for word, score in keyword_dict['Biology'']:
    print(f"{word}: {score:.4f}")
'''

[[['poema', 'janus', '', '', 'janus', 'gulielmius', '', 'ualeo', 'acidalius', '', 'nouus', 'editio', ''], ['lignix', 'impensa', 'dauidus', 'alipertus', 'bibliopolas', 'uratisl', ''], ['annus', 'cio', 'io', 'ciiius', ''], ['u', '', '', 'icus', 'nobilissimus', 'excello', 'doctrina', '', 'uirtus', 'uiris', 'd', 'jacobus', '', 'consiliarius', 'ligiobregensis', '', '', 'd', 'daniel', 'rindfleisch', 'bucretiocphilosophus', 'et', 'medicoi', 'patritius', 'uratislauiensibus', '', 'dominus', '', 'patronum', 'obseruo', 'caspar', '', '', 'uratislauiense', 's', 'd', 'agna', 'apud', 'pius', 'antiquitas', 'poeta', 'semper', 'sum', 'existimatio', '', 'uiri', 'nobilissimus', '', 'lu', 'magnus', 'reuerentia', 'atque', 'obseruo', ''], ['praeter', 'hic', 'enim', '', 'qui', 'primus', 'phiiosophiaa', 'magistrus', '', '', 'musons', '', 'hinc', 'inde', 'nuncupo', ''], ['filius', 'etiam', 'deus', '', 'deus', 'interpres', '', 'propheta', '', 'pater', 'sapientia', '', 'uirtus', 'genitor', 'ab', 'plato', 'magnus'

FileNotFoundError: [Errno 2] No such file or directory: 'texts/1479057.json'